In [26]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

In [27]:
import plotly.io as pio

pio.renderers.default = "vscode"  # or "vscode" if using VS Code notebooks

template = pio.templates["plotly_dark"]

# Backgrounds
template.layout.plot_bgcolor = "#2B2B2B"   # inside the axes
template.layout.paper_bgcolor = "#2B2B2B"  # around the plot

# X axis
template.layout.xaxis.color = "#A9B7C6"    # tick labels + title
template.layout.xaxis.gridcolor = "#7B7E82"
template.layout.xaxis.showline = False
template.layout.xaxis.linecolor = "#A9B7C6"
template.layout.xaxis.tickcolor = "#A9B7C6"  # color of tick lines
template.layout.xaxis.zeroline = False
template.layout.xaxis.zerolinecolor = "#A9B7C6"

# Y axis
template.layout.yaxis.color = "#A9B7C6"
template.layout.yaxis.gridcolor = "#7B7E82"
template.layout.yaxis.showline = False
template.layout.yaxis.linecolor = "#A9B7C6"
template.layout.yaxis.tickcolor = "#A9B7C6"
template.layout.yaxis.zeroline = False
template.layout.yaxis.zerolinecolor = "#A9B7C6"

# Register as new template
pio.templates["custom_dark"] = template
pio.templates.default = "custom_dark"

## **1.0 Train/Test split**

In [32]:
df = pd.read_csv("labelled_features.csv", parse_dates=["timestamp"]).reset_index(drop=True)

# Ensure timestamp is datetime
df["timestamp"] = pd.to_datetime(df["timestamp"])

# If `date` is not already datetime (but sounds like it is):
df["date"] = pd.to_datetime(df["date"])
# Sort by time to respect chronology
df = df.sort_values(["ticker", "timestamp"]).reset_index(drop=True)

# Drop rows where the target is missing
df = df.dropna(subset=["label_cascade"])

In [33]:
# Define split dates
train_end   = "2024-12-31"
valid_start = "2025-01-01"
valid_end   = "2025-03-15"
test_start  = valid_end  # test = from here onwards

# Build the splits
df_train = df[df["date"] <  train_end].copy()
df_valid = df[(df["date"] >= valid_start) & (df["date"] < valid_end)].copy()
df_test  = df[df["date"] >= test_start].copy()

print(len(df_train), len(df_valid), len(df_test))

76787 16249 84470


## **2.0 Feature selection and cleaning**

### **2.1 Drop any columns not available at prediction time**
- drop any forward looking information
- also drop identifiers or raw prices, keep engineered features only

In [34]:
cols_to_exclude = [
    "ticker",        # identifier
    "timestamp",
    "date",
    "label_cascade", # target
    "fwd_dd_log_H"   # forward-looking metric (for evaluation only)
]

feature_cols = [c for c in df.columns if c not in cols_to_exclude]

print("Number of features:", len(feature_cols))
print(feature_cols)

Number of features: 67
['open', 'high', 'low', 'close', 'volume', 'vwap', 'num_trades', 'missing_bars_day', 'logret', 'logret_2', 'logret_3', 'logret_5', 'logret_10', 'body', 'upper_wick', 'lower_wick', 'hl_range', 'rv_5', 'rv_10', 'rv_20', 'rv_50', 'parkinson_bar', 'parkinson_20', 'atr_5', 'atr_50', 'compression_atr', 'volume_ma_5', 'volume_z_5', 'volume_ma_20', 'volume_z_20', 'volume_ma_50', 'volume_z_50', 'trades_ma_5', 'trades_z_5', 'trades_ma_20', 'trades_z_20', 'price_move_abs', 'volume_per_trade', 'move_per_volume', 'move_per_trade', 'efficiency', 'impact_lambda', 'signed_volume', 'dist_vwap', 'dist_vwap_pct', 'vwap_slope', 'vwap_slope2', 'logret_QQQ', 'logret_SPY', 'rel_ret_SPY', 'rel_ret_QQQ', 'corr_SPY', 'corr_QQQ', 'ret_sign', 'market_breadth', 'minute_of_session', 'minute_sin', 'minute_cos', 'is_open', 'is_close', 'is_midday', 'skew_20', 'kurt_20', 'downside_vol_20', 'downside_ratio_20', 'sigma_park', 'sigma_ret_20']


In [35]:
# feature_cols = ['is_close', 'minute_cos', 'rv_5', 'rv_20', 'sigma_ret_20', 'kurt_20', 'minute_sin', 'is_open', 'logret_10', 'rv_10', 'downside_vol_20', 'trades_ma_20', 'volume_ma_20', 'atr_5', 'rv_50', 'downside_ratio_20', 'corr_SPY', 'move_per_trade', 'volume_z_50', 'skew_20']

### **2.2 Handle categorical features**
- later one-hot encode the tickers

### **2.3 Build X and y matrices for train, valid and test**

In [36]:
# --- TEST SET ---

X_test = df_test[feature_cols]
y_test = df_test["label_cascade"].astype(int)

X_test = X_test.replace([np.inf, -np.inf], np.nan)

mask_test = X_test.notna().all(axis=1)

X_test = X_test[mask_test]
y_test = y_test[mask_test]
df_test = df_test.loc[mask_test].copy()

# TRAIN
X_train = df_train[feature_cols]
y_train = df_train["label_cascade"].astype(int)

X_train = X_train.replace([np.inf, -np.inf], np.nan)
mask_train = X_train.notna().all(axis=1)

X_train = X_train[mask_train]
y_train = y_train[mask_train]
df_train = df_train.loc[mask_train].copy()

# VALID
X_valid = df_valid[feature_cols]
y_valid = df_valid["label_cascade"].astype(int)

X_valid = X_valid.replace([np.inf, -np.inf], np.nan)
mask_valid = X_valid.notna().all(axis=1)

X_valid = X_valid[mask_valid]
y_valid = y_valid[mask_valid]
df_valid = df_valid.loc[mask_valid].copy()

### **2.4 Standardise all Features**
- logistic regression requires standardisation
- prevents large-scale features from dominating

In [37]:
X_train

open      high      low     close     volume      vwap  num_trades  \
0       190.741  190.9900  190.720  190.9550   269657.0  190.9084        3652   
1       190.950  191.0750  190.920  190.9250   331877.0  191.0113        4246   
2       190.935  190.9550  190.815  190.9000   292408.0  190.8904        3538   
3       190.320  190.3900  190.310  190.3100     2098.0  190.3480          54   
4       188.160  188.2800  187.850  187.9050  1330530.0  188.0792       31532   
...         ...       ...      ...       ...        ...       ...         ...   
167171  424.320  424.5000  423.610  423.9200    15751.0  424.1318         747   
167172  421.730  422.7000  419.000  419.1155   879503.0  420.8163       16264   
167173  419.240  419.7300  417.390  418.0206   882351.0  418.4023       19282   
167174  418.120  420.1699  418.000  420.1699   700369.0  419.2820       13024   
167175  420.020  420.1799  418.500  419.5987   562813.0  419.4037       10327   

        missing_bars_day    logret  logret_2  ...  minute_cos  is_open  \
0                      8  0.001100  0.001048  ...    0.987050        0   
1                      8 -0.000157  0.000943  ...    0.996757        0   
2                      8 -0.000131 -0.000288  ...    1.000000        0   
3                      9 -0.000053  0.000053  ...    0.970942        1   
4                      9 -0.001356 -0.003215  ...    0.885456        0   
...                  ...       ...       ...  ...         ...      ...   
167171                 0 -0.000707 -0.026307  ...    0.996757        1   
167172                 0 -0.006349 -0.008043  ...    0.970942        0   
167173                 0 -0.002616 -0.008965  ...    0.987050        0   
167174                 0  0.005128  0.002513  ...    0.996757        0   
167175                 0 -0.001360  0.003768  ...    1.000000        0   

        is_close  is_midday   skew_20   kurt_20  downside_vol_20  \
0              1          0  1.758416  4.116436         0.002881   
1              1          0  1.782608  4.160082         0.002886   
2              1          0  1.781007  4.158311         0.002885   
3              0          0 -1.140719  1.678857         0.004260   
4              0          0 -0.037225 -0.222837         0.005241   
...          ...        ...       ...       ...              ...   
167171         0          0 -1.628443  3.051414         0.032220   
167172         1          0  0.314470 -0.421914         0.014268   
167173         1          0  0.311096 -0.414271         0.014232   
167174         1          0  0.248824 -0.655391         0.014232   
167175         1          0  0.263417 -0.660474         0.014271   

        downside_ratio_20  sigma_park  sigma_ret_20  
0                0.488622    0.001210      0.001349  
1                0.489244    0.001210      0.001350  
2                0.489110    0.001212      0.001350  
3                0.935554    0.000763      0.000969  
4                0.896392    0.001194      0.001235  
...                   ...         ...           ...  
167171           0.953583    0.004553      0.007304  
167172           0.702851    0.005007      0.004648  
167173           0.701959    0.005043      0.004643  
167174           0.682816    0.005081      0.004781  
167175           0.683819    0.005105      0.004786  

[76787 rows x 67 columns]

In [38]:
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()

X_train_scaled = scaler.fit_transform(X_train)
X_valid_scaled = scaler.transform(X_valid)
X_test_scaled  = scaler.transform(X_test)

## **3.0 Handle class imbalance**
- since cascades only happen roughly 5% of the time, we need to adjust for that in our linear model

In [39]:
from sklearn.linear_model import LogisticRegression

clf = LogisticRegression(
    penalty="l2",
    C=5.0,
    class_weight="balanced",
    max_iter=1000
)

## **4.0 Train the model**

In [40]:
from sklearn.linear_model import LogisticRegression

clf = LogisticRegression(
    penalty="l2",
    C=1.0,
    class_weight="balanced",  # adjusts for rare cascades
    max_iter=10000,
    solver="lbfgs",
    n_jobs=-1  # use all cores if available
)

clf.fit(X_train_scaled, y_train)

LogisticRegression(class_weight='balanced', max_iter=10000, n_jobs=-1)

## **5.0 Model Evaluation**

### **5.1 Compute Basic metrics**

In [41]:
from sklearn.metrics import (
    roc_auc_score, roc_curve,
    average_precision_score, precision_recall_curve,
    brier_score_loss
)

# Predicted probabilities for the positive class
probs_train = clf.predict_proba(X_train_scaled)[:, 1]
probs_valid = clf.predict_proba(X_valid_scaled)[:, 1]
probs_test  = clf.predict_proba(X_test_scaled)[:, 1]

# --- AUC / AP on test set ---
auc_test = roc_auc_score(y_test, probs_test)
ap_test = average_precision_score(y_test, probs_test)
brier = brier_score_loss(y_test, probs_test)

print(f"Test ROC AUC:         {auc_test:.3f}")
print(f"Test Average Precision: {ap_test:.3f}")
print(f"Test Brier score:     {brier:.4f}")

Test ROC AUC:         0.805
Test Average Precision: 0.138
Test Brier score:     0.1916


#### ROC AUC - Receiver Operating Characteristics, Area Under Curve
- Essentially just tells you how well the model is ranking bars by how likely a crach is to occur
- AUC = P(model gives a higher score to a random cascade than a random non-cascade)
- Here we have an AUC of 0.805 so the model has a strong ability to distinguish cascade bars from normal ones

#### Test Average Precision
- Average precision measures the area under the precision-recall curve
    - High precision means - when the model says there will be a cascade, it's usually right
    - High recall means - how many real cascades do we catch
- Since cascades are < 5% of all bars, AUC can be misleading
- We have an AP of ~0.14, which is **very good** for our cascade bar event rate
- This AP is around **4x** better than random (since actual cascade rate is ~4%)

#### Brier Score
- Measures the accuracy of probability predictions
- Combines calibration, resolution and reliability
- Currently we have quite a high Brier score ~20%, suggesting our model probabilities do not reflect the actual probabilities of seeing events
- So we may need to calibrate the model (see later)

**Having a low Brier score is crucial for things like position sizing and hedging**


### **5.2 Plot true positive rates vs false positive rates**
- good models hug the top left corner

In [42]:
# Compute ROC curve
fpr, tpr, roc_thresholds = roc_curve(y_test, probs_test)

fig_roc = go.Figure()

# Model ROC
fig_roc.add_trace(go.Scatter(
    x=fpr, y=tpr, mode="lines",
    name=f"LogReg (AUC={auc_test:.3f})"
))

# Diagonal random baseline
fig_roc.add_trace(go.Scatter(
    x=[0, 1], y=[0, 1],
    mode="lines",
    name="Random",
    line=dict(dash="dash")
))

fig_roc.update_layout(
    title="ROC Curve (Test Set)",
    xaxis_title="False Positive Rate",
    yaxis_title="True Positive Rate",
    xaxis=dict(range=[0, 1]),
    yaxis=dict(range=[0, 1]),
)

fig_roc.show()

### **5.3 Plot precision-recall curve**
- with rare cascades, precision-recall curves are more informative
    - Precision: when you trigger, how often are you right
    - Recall: how many of all cascades do you catch

In [43]:
precision, recall, pr_thresholds = precision_recall_curve(y_test, probs_test)

fig_pr = go.Figure()

fig_pr.add_trace(go.Scatter(
    x=recall[:-1], y=precision[:-1],
    mode="lines",
    name=f"LogReg (AP={ap_test:.3f})"
))

# Baseline: prevalence of class 1 in test set
base_rate = y_test.mean()
fig_pr.add_trace(go.Scatter(
    x=[0, 1], y=[base_rate, base_rate],
    mode="lines",
    name=f"Base rate = {base_rate:.4f}",
    line=dict(dash="dash")
))

fig_pr.update_layout(
    title="Precision-Recall Curve (Test Set)",
    xaxis_title="Recall",
    yaxis_title="Precision",
    xaxis=dict(range=[0, 1]),
    yaxis=dict(range=[0, 0.2]),
)

fig_pr.show()

- at peak, we have a recall of about 30% at a precision of ~18%

    - This means that if we assign a cascade signal to the top 30% "most risky" bars, 18% of the trades catch a cascade
    - 18% of cascades are caught even though cascades only happen 4.3% of the time (base rate)
    - This is roughly **8x** better than random

- If we set the recall to 1.00 (we assign everything a cascade), our precision falls to exactly the base rate
- If we drop the threshold to 0.6, so that our model catches 60% of all cascades, we get a precision of 14%
    - This is still nearly **4x** better than random

### **5.4 Probability Distrubution per class**
- looking for if the model is assigning higher probabilities to cascades over non-cascades
- hopefully this will produce a nice separation!

In [44]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# Split probabilities by actual class
probs_pos = probs_test[y_test == 1]
probs_neg = probs_test[y_test == 0]

# Create figure with secondary y-axis
fig_hist = make_subplots(specs=[[{"secondary_y": True}]])

# Non-cascade (y=0) on primary y-axis
fig_hist.add_trace(
    go.Histogram(
        x=probs_neg,
        nbinsx=50,
        name="Non-cascade",
        opacity=0.5
    ),
    secondary_y=False
)

# Cascade (y=1) on secondary y-axis
fig_hist.add_trace(
    go.Histogram(
        x=probs_pos,
        nbinsx=30,
        name="Cascade",
        opacity=0.5
    ),
    secondary_y=True
)

fig_hist.update_layout(
    barmode="overlay",  # still overlay the bars
    title="Distribution of Predicted Probabilities by Class (Test)",
    xaxis_title="Predicted P(cascade)",
)

# Label y-axes separately
fig_hist.update_yaxes(
    title_text="Count (non-cascade)",
    secondary_y=False
)
fig_hist.update_yaxes(
    title_text="Count (cascade)",
    secondary_y=True
)

fig_hist.show()

- in the histograms we see that the model assigns high probabilities to cascade events
    - this shows that the model has some predictive power, and if the predicted cascade probability is high, there often is actually a cascade
    - non-cascade events have probabilities clustered near zero (though there is a very long fat tail out to the right)
    

### **5.5 Calibration Curve**
- We don't just care about the ranking but also:
    - When you say P(cascade) = 0.8, does it really happen 0.8% of the time?
- Bucket predictions into bins and compare mean predicted probability vs observed frequency

In [45]:
def calibration_curve_df(y_true, y_prob, n_bins=10):
    df_cal = pd.DataFrame({"y": y_true, "p": y_prob})
    df_cal["bin"] = pd.qcut(df_cal["p"], q=n_bins, duplicates="drop")
    
    grouped = df_cal.groupby("bin", observed=True).agg(
        mean_pred=("p", "mean"),
        frac_positive=("y", "mean"),
        count=("y", "size")
    ).reset_index(drop=True)
    
    return grouped

cal_df = calibration_curve_df(y_test, probs_test, n_bins=10)

fig_cal = go.Figure()

fig_cal.add_trace(go.Scatter(
    x=cal_df["mean_pred"],
    y=cal_df["frac_positive"],
    mode="lines+markers",
    name="Model"
))

# Perfect calibration line
fig_cal.add_trace(go.Scatter(
    x=[0, 1], y=[0, 1],
    mode="lines",
    name="Perfect calibration",
    line=dict(dash="dash")
))

fig_cal.update_layout(
    title="Calibration Curve (Test Set)",
    xaxis_title="Mean Predicted Probability",
    yaxis_title="Observed Frequency of Cascades",
    xaxis=dict(range=[0, 1]),
    yaxis=dict(range=[0, 1]),
)

fig_cal.show()

cal_df

mean_pred  frac_positive  count
0   0.006841       0.004262   8447
1   0.034851       0.002960   8447
2   0.103246       0.006630   8447
3   0.180783       0.008761   8447
4   0.279754       0.020481   8447
5   0.387164       0.025926   8447
6   0.491165       0.041553   8447
7   0.600249       0.050906   8447
8   0.700120       0.101693   8447
9   0.819307       0.168344   8447

- the above shows that the model is ***wildly overconfident*** when it comes to predicting cascades:

    - Sometimes the model will say that the probability of a cascade is 80%, when the actual true frequency is only 13%

- So the model is poorly calibrated
- **However**, the montonic nature of the line shows that the ordering of the probabilities is good, it is just far too sure of itself when it thinks a cascade is coming

#### **Calibrate the model using isotonic regression to reduce overconfidence**

In [46]:
from sklearn.isotonic import IsotonicRegression

iso = IsotonicRegression(out_of_bounds="clip")

# Fit only on validation set!
iso.fit(probs_valid, y_valid)

# Apply calibration
probs_test_cal = iso.transform(probs_test)

print("roc_auc: ", roc_auc_score(y_test, probs_test_cal))
print("average_precision: ", average_precision_score(y_test, probs_test_cal))
print("brier: ",brier_score_loss(y_test, probs_test_cal))

print("Unique raw probs:", np.unique(probs_test).shape[0])
print("Unique cal probs:", np.unique(probs_test_cal).shape[0])
print("PR points:", len(precision), len(recall))

roc_auc:  0.7887893054181904
average_precision:  0.1254585276567175
brier:  0.03938452323105067
Unique raw probs: 84470
Unique cal probs: 111
PR points: 84471 84471


little change to roc auc, and average precision, but an order of magnitude better brier score (so huge improvement in calibration)

In [47]:
cal_df = calibration_curve_df(y_test, probs_test_cal, n_bins=10)

fig_cal = go.Figure()

fig_cal.add_trace(go.Scatter(
    x=cal_df["mean_pred"],
    y=cal_df["frac_positive"],
    mode="lines+markers",
    name="Model"
))

# Perfect calibration line
fig_cal.add_trace(go.Scatter(
    x=[0, 1], y=[0, 1],
    mode="lines",
    name="Perfect calibration",
    line=dict(dash="dash"),
))

fig_cal.update_layout(
    title="Calibration Curve (Test Set)",
    xaxis_title="Mean Predicted Probability",
    yaxis_title="Observed Frequency of Cascades",
    xaxis=dict(range=[0, 0.15]),
    yaxis=dict(range=[0, 0.2]),
)
fig_cal.update_layout(template="plotly_white")

fig_cal.show()

cal_df

mean_pred  frac_positive  count
0   0.000253       0.003992  12777
1   0.002606       0.002980   4362
2   0.003036       0.006453  10382
3   0.011228       0.009540   6394
4   0.068867       0.039679  37375
5   0.097277       0.119400   6005
6   0.132130       0.174634   7175

- above we see a much better calibrated model, with the line fitting very close to the perfect calibration line, orders of magnitude better

- we can also see that the probability values have been massively compressed into the bottom left of the graph (low observed and predicted probabilities)
    - this makes sense as the **observed probabilities of cascades are incredibly low**
    - therefore our probability score for how likely a cascade is at time t should be a lot lower than what we previously had, which was in the order of 80%

In [48]:
from sklearn.metrics import precision_recall_curve, average_precision_score

# Pre-calibration
prec_raw, rec_raw, _ = precision_recall_curve(y_test, probs_test)
ap_raw = average_precision_score(y_test, probs_test)

# Post-calibration
prec_cal, rec_cal, _ = precision_recall_curve(y_test, probs_test_cal)
ap_cal = average_precision_score(y_test, probs_test_cal)

import plotly.graph_objects as go

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=rec_raw[:-1], y=prec_raw[:-1],
    mode="lines",
    name=f"Raw (AP={ap_raw:.3f})",
))

fig.add_trace(go.Scatter(
    x=rec_cal[:-1], y=prec_cal[:-1],
    mode="lines",
    name=f"Calibrated (AP={ap_cal:.3f})",
))

base_rate = y_test.mean()
fig.add_trace(go.Scatter(
    x=[0, 1], y=[base_rate, base_rate],
    mode="lines",
    name=f"Base rate = {base_rate:.4f}",
    line=dict(dash="dash")
))

fig.update_layout(
    title="Precision-Recall Curve: Raw vs Calibrated",
    xaxis_title="Recall",
    yaxis_title="Precision",
    xaxis=dict(range=[0, 1]),
    yaxis=dict(range=[0, 0.2])
)

fig.show()

In [49]:
len_probs = len(probs_test_cal)
n_unique = np.unique(probs_test_cal).shape[0]
print("Total scores:", len_probs)
print("Unique scores:", n_unique)               
print("Precision length:", len(precision))     

Total scores: 84470
Unique scores: 111
Precision length: 84471


## **6.0 Forming a backtesting Strategy**
- We now have a model that is fairly good at saying "there will be a bad drop somewhere in the next H bars (H=6)"
- To turn this into a profitable strategy we need to:
    1. Decide what to actual try to monetise
    2. Design execution rules that actually capture path risk
    3. Use the model as a filter/position sizer

In [50]:
clf.coef_

array([[ 0.01098112,  0.010912  ,  0.01079306,  0.01072534, -0.01354099,
         0.01073925, -0.13059517, -0.03772766,  0.04617472,  0.020523  ,
        -0.09513065, -0.0251444 ,  0.26749341, -0.1077682 ,  0.04370231,
         0.03575931,  0.03563095,  0.69824259, -0.24944098, -0.62027539,
         0.16082461, -0.10132051, -0.00745571, -0.16514036,  0.0550787 ,
        -0.11556516,  0.1319609 ,  0.02788977, -0.16851886, -0.06035439,
         0.08159907,  0.14117234,  0.01803927,  0.00386149,  0.16854276,
         0.11492072,  0.03563095, -0.03761829, -0.00635221, -0.14238115,
         0.04992403, -0.10103359, -0.04086023, -0.00857637, -0.02546757,
        -0.06395966,  0.02350926, -0.01223723,  0.05972506,  0.0313567 ,
         0.06191774, -0.15371241, -0.06064514, -0.02751184, -0.03827602,
        -0.08719405, -0.40421138, -1.01895774, -0.3317003 ,  1.33755048,
         0.        ,  0.14041908, -0.41553216,  0.19558561,  0.15433899,
        -0.07910444, -0.5937032 ]])

In [51]:
import numpy as np
import pandas as pd

# Coefficients for the positive class (shape: (n_features,))
coef = clf.coef_[0]

feat_imp = pd.DataFrame({
    "feature": feature_cols,
    "coef": coef
})

# Add absolute value for sorting
feat_imp["coef_abs"] = feat_imp["coef"].abs()

# Sort by absolute importance, descending
feat_imp = feat_imp.sort_values("coef_abs", ascending=False).reset_index(drop=True)

feat_imp.head(20)

feature      coef  coef_abs
0            is_close  1.337550  1.337550
1          minute_cos -1.018958  1.018958
2                rv_5  0.698243  0.698243
3               rv_20 -0.620275  0.620275
4        sigma_ret_20 -0.593703  0.593703
5             kurt_20 -0.415532  0.415532
6          minute_sin -0.404211  0.404211
7             is_open -0.331700  0.331700
8           logret_10  0.267493  0.267493
9               rv_10 -0.249441  0.249441
10    downside_vol_20  0.195586  0.195586
11       trades_ma_20  0.168543  0.168543
12       volume_ma_20 -0.168519  0.168519
13              atr_5 -0.165140  0.165140
14              rv_50  0.160825  0.160825
15  downside_ratio_20  0.154339  0.154339
16           corr_SPY -0.153712  0.153712
17     move_per_trade -0.142381  0.142381
18        volume_z_50  0.141172  0.141172
19            skew_20  0.140419  0.140419

In [52]:
top_k = 25
top = feat_imp.head(top_k).sort_values("coef", ascending=True)

fig = go.Figure()

fig.add_trace(go.Bar(
    x=top["coef"],
    y=top["feature"],
    orientation="h",
))

fig.update_layout(
    title=f"Top {top_k} Logistic Regression Coefficients",
    xaxis_title="Coefficient (impact on log-odds)",
    yaxis_title="Feature",
)
fig.update_yaxes(showticklabels=True)
fig.update_layout(
    height=25 * len(top)
)
fig.show()